# BM25 & Cross Encoder & Bi Encoder

Mr-tydi dataset을 통해 bm25, cross encoder, bi encoder를 비교한다.


In [1]:
!pip install -U transformers datasets sentence-transformers rank_bm25

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.9/7.9 MB 19.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 493.7/493.7 kB 33.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 kB 13.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 311.1/311.1 kB 40.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 54.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 24.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 13.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 19.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 41.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 295.0/295.0 kB 9.4 MB/s eta 0:00:00
  Created wheel for sentence-transformers: filename=sentence_transformers-2.2.2-py3-none-any.whl size=125923 sha256=e91562ab2e5a387b31941229c670b911

In [3]:
import json
from sentence_transformers import SentenceTransformer, CrossEncoder, util
import gzip
import os
import torch

if not torch.cuda.is_available():
    print("Warning: No GPU found. Please add GPU to your notebook")


# Bi-encoder
bi_encoder = SentenceTransformer('intfloat/multilingual-e5-large')
bi_encoder.max_seq_length = 512     # 512개로 truncation
top_k = 32

# bi-encoder로 100개 검색 후에, quality를 향상시키기 위해 re-rank한다.
cross_encoder = CrossEncoder('bongsoo/albert-small-kor-cross-encoder-v1')

In [4]:
from datasets import load_dataset

In [5]:
dataset = load_dataset('castorini/mr-tydi', 'korean')

Extracting data files:   0%|          | 0/3 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating dev split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

In [6]:
train_dataset = dataset['train']

In [7]:
passages = []
for one in train_dataset:
  for pos_one in one['positive_passages']:
    title, text = pos_one['title'], pos_one['text']
    passage = f"{title} {text}"
    passages.append(passage)
  # for pos_one in one['negative_passages']:
  #   title, text = pos_one['title'], pos_one['text']
  #   passage = f"{title} {text}"
  #   passages.append(passage)
passages = list(set(passages))
len(passages)

1059

In [8]:
passages[:3]

['베네수엘라 베네수엘라 볼리바르 공화국(), 약칭 베네수엘라()는 남아메리카에 있는 나라이다. 스페인어를 공용어로 사용하며, 수도는 카라카스이다.',
 '람보르기니 디아블로 람보르기니 디아블로(Lamborghini Diablo)는 이탈리아의 자동차 제조업체 람보르기니가 1990년부터 2001년까지 생산한 스포츠 자동차이다. 미드쉽 엔진 차체에 후륜구동 자동차가 있으며, 람보르기니 최초로 사륜구동이 채택된 자동차이다. 또한 람보르기니 최초로 최고속도가 320 km/h (200 mph)에 도달한 자동차이다. 팝업 전조등이 구비된 차량이 1세대이며 개방형 전조등이 구비된 차량이 2세대이다. 2001년에 후속차량인 람보르기니 무르시엘라고에게 자리를 넘겨주고 단종되었다.',
 '남아프리카 공화국 북쪽으로는 나미비아, 보츠와나, 짐바브웨와 접해 있으며 북동쪽으로는 모잠비크, 에스와티니와 접한다. 1966년에 독립한 내륙국인 레소토가 남아프리카 공화국 영토 안에 둘러싸여 있다. 수도는 3개로 행정 수도는 프리토리아, 입법 수도는 케이프타운, 사법 수도는 블룸폰테인이다.']

In [9]:
# We encode all passages into our vector space. This takes about 5 minutes (depends on your GPU speed)
corpus_embeddings = bi_encoder.encode(passages, convert_to_tensor=True, show_progress_bar=True)

Batches:   0%|          | 0/34 [00:00<?, ?it/s]

In [10]:
# We also compare the results to lexical search (keyword search). Here, we use
# the BM25 algorithm which is implemented in the rank_bm25 package.

from rank_bm25 import BM25Okapi
import string
from tqdm.autonotebook import tqdm
import numpy as np

stop_words = ["하고", "하려면", "해서", "가까스로", "각자", "각각", "것들",
              "그때", "그래도", "그래서", "그러나", "그러니까", "그러므로",
              "그런데", "약간"]  # 잘 추가하면 성능 올라감.

# We lower case our text and remove stop-words from indexing
def bm25_tokenizer(text):
    tokenized_doc = []
    for token in text.lower().split():
        token = token.strip(string.punctuation)

        if len(token) > 0 and token not in stop_words:
            tokenized_doc.append(token)
    return tokenized_doc


tokenized_corpus = []
for passage in tqdm(passages):
    tokenized_corpus.append(bm25_tokenizer(passage))

bm25 = BM25Okapi(tokenized_corpus)


  0%|          | 0/1059 [00:00<?, ?it/s]

In [11]:
# This function will search all wikipedia articles for passages that
# answer the query
def search(query):
    print("Input question:", query)

    ##### BM25 search (lexical search) #####
    bm25_scores = bm25.get_scores(bm25_tokenizer(query))
    top_n = np.argpartition(bm25_scores, -5)[-5:]
    bm25_hits = [{'corpus_id': idx, 'score': bm25_scores[idx]} for idx in top_n]
    bm25_hits = sorted(bm25_hits, key=lambda x: x['score'], reverse=True)

    print("Top-3 lexical search (BM25) hits")
    for hit in bm25_hits[0:3]:
        print("\t{:.3f}\t{}".format(hit['score'], passages[hit['corpus_id']].replace("\n", " ")))

    ##### Sematic Search #####
    # Encode the query using the bi-encoder and find potentially relevant passages
    question_embedding = bi_encoder.encode(query, convert_to_tensor=True)
    question_embedding = question_embedding.cuda()
    hits = util.semantic_search(question_embedding, corpus_embeddings, top_k=top_k)
    hits = hits[0]  # Get the hits for the first query

    ##### Re-Ranking #####
    # Now, score all retrieved passages with the cross_encoder
    cross_inp = [[query, passages[hit['corpus_id']]] for hit in hits]
    cross_scores = cross_encoder.predict(cross_inp)

    # Sort results by the cross-encoder scores
    for idx in range(len(cross_scores)):
        hits[idx]['cross-score'] = cross_scores[idx]

    # Output of top-5 hits from bi-encoder
    print("\n-------------------------\n")
    print("Top-3 Bi-Encoder Retrieval hits")
    hits = sorted(hits, key=lambda x: x['score'], reverse=True)
    for hit in hits[0:3]:
        print("\t{:.3f}\t{}".format(hit['score'], passages[hit['corpus_id']].replace("\n", " ")))

    # Output of top-5 hits from re-ranker
    print("\n-------------------------\n")
    print("Top-3 Cross-Encoder Re-ranker hits")
    hits = sorted(hits, key=lambda x: x['cross-score'], reverse=True)
    for hit in hits[0:3]:
        print("\t{:.3f}\t{}".format(hit['cross-score'], passages[hit['corpus_id']].replace("\n", " ")))


In [18]:
search(query = train_dataset[3]['query'])

Input question: 히틀러는 몇 년도에 사망했는가?
Top-3 lexical search (BM25) hits
	8.387	아돌프 히틀러 아돌프 히틀러는 1889년 4월 20일에 독일과 오스트리아 사이를 흐르는 인 강(Inn)과 접한 오스트리아의 브라우나우암인(Braunau am Inn)에서 6남매 중 4번째 아이로 태어났다. 아돌프는 어릴적 '아디'라고 불렸으며 '볼프'라는 별명도 있었다. 세무 공무원이었으나 학력이 낮았던 아버지 알로이스 히틀러는 술꾼에 무례하고 권위주의적이고 흉폭했다고 한다. 어머니 클라라 푈츨(Klara Pölzl, 1860 ~ 1907)은 알로이스 히틀러의 외조카이자 였는데 병약하였다. 일부 학자들은 히틀러의 난폭한 성격과 행동의 원인을 어린 시절 아버지에게서 받은 폭력에서 찾으려 하기도 한다.
	6.906	아돌프 히틀러 승승장구하며 전세를 확장하던 독일은 스탈린그라드 전투와 북아프리카 전선에서 패배하였고, 히틀러는 1945년 4월 29일 소련군에 포위된 베를린에서 자신의 연인이었던 에바 브라운과 결혼한 뒤 이튿날 베를린의 총통관저 지하 벙커에서 시안화칼륨 캡슐을 삼키고 권총으로 자신을 쏘아 자살했다.[1] 그러나 독약 캡슐을 쓰지 않고 권총 자살을 했다는 이야기도 있다.[2]
	5.179	오페스 오페스(Opeth)는 1989년 스웨덴의 스톡홀름에서 결성된 메탈 밴드이다.[1][2] 밴드는 몇 차례의 구성원 변화를 겪었지만 리드 보컬/기타리스트/송라이터인 미카엘 오케르펠트는 꾸준히 오페스의 원동력 역할을 하고 있다. 오페스는 작곡에 초기에 데스 메탈으로부터 강한 영향을 받은 것과 같이, 계속해서 프로그레시브, 포크, 블루스, 클래식, 재즈의 요소들을 차용한다. 대부분의 곡이 그로울링과 클린 보컬 뿐만아니라 어쿠스틱 기타 연주을 포함한다. 또한 그들의 곡은 대부분 곡조의 변화가 역동적이다. 오페스는 멜로트론을 활용하여 곡을 쓰는 것으로도 유명하다. 오페스는 그들의 초기 4개 음반 시절에는 라이브 공연을 잘 하지 않았으나 2001

In [13]:
search(query = "철학적 자연주의의 이론이 처음으로 등장한 것은 언제인가요?")

Input question: 철학적 자연주의의 이론이 처음으로 등장한 것은 언제인가요?
Top-3 lexical search (BM25) hits
	36.034	자연주의 (철학) 철학적 자연주의의 이론이 처음으로 등장한 것은 이오니아의 소크라테스 이전 철학자들의 글이었다. 특별히 과학의 아버지로 불리는 탈레스가 처음으로 자연현상을 초자연적인 원인을 사용하지 않고 설명했다. 초기 그리스 철학에 대한 조너선 바르네스(Jonathan Barnes)의 소개는 이러한 초기 철학자들을, 자연주의를 미리 예견이라도 한 것처럼 경험적인 원리에 따라 자연을 연구한 사람들로 묘사하고 있다.
	6.397	오행 오행(五行, )은 동양 철학에서 우주 만물의 변화양상을 5가지로 압축해서 설명하는 이론으로[1], 5행이라는 것은 인간 사회의 다섯 개 원소로 생각된 화(火)·수(水)·목(木)·금(金)·토(土)의 운행변전(運行變轉)을 말한다. 행(行)이라는 것은 운행의 뜻이다.
	6.190	외뿔소자리 V838 외뿔소자리 V838은 외뿔소자리에 있는 변광성으로 지구에서 약 2만 광년 떨어져 있다.[1] 이 별은 2002년 초에 큰 폭발을 일으켰다. 처음에는 이 폭발을 전형적인 신성 폭발 현상으로 여겼으나, 이후 신성과는 다른 성질의 폭발임을 알게 되었다. 폭발의 정확한 원인은 아직까지 규명되지 않았으나 몇 가지 이론이 제기된 상태이다. 예로써 항성이 죽어가는 과정이거나, 동반성 혹은 행성들을 빨아들여 생긴 현상이라는 것 등이 있다.

-------------------------

Top-3 Bi-Encoder Retrieval hits
	0.874	자연주의 (철학) 철학적 자연주의의 이론이 처음으로 등장한 것은 이오니아의 소크라테스 이전 철학자들의 글이었다. 특별히 과학의 아버지로 불리는 탈레스가 처음으로 자연현상을 초자연적인 원인을 사용하지 않고 설명했다. 초기 그리스 철학에 대한 조너선 바르네스(Jonathan Barnes)의 소개는 이러한 초기 철학자들을, 자연주의를 미리 예견이라도 

In [14]:
print(train_dataset[0]['query'])
print(train_dataset[0]['positive_passages'][0])

로마의 면적은 서울시의 2배인가요?
{'docid': '3228#0', 'text': '로마()는 이탈리아의 수도이자 라치오주의 주도로, 테베레 강 연안에 있다. 로마시의 행정구역 면적은 1,285km2로 서울시의 2배정도이고, 2014년 인구는 290여만명이다. 로마시 권역의 인구는 430여만명이다. [1] 로마 대도시현의 인구는 400만이 넘지만 밀라노나 나폴리 대도시현에 비해 면적이 3~4배 넓은 편이고 되려 로마시의 면적과 밀라노와 나폴리의 대도시현의 면적이 비슷하므로 세 도시 모두 300만 정도로 비슷한 규모의 도시라 볼 수 있다.', 'title': '로마'}


In [15]:
search(query = train_dataset[0]['query'])

Input question: 로마의 면적은 서울시의 2배인가요?
Top-3 lexical search (BM25) hits
	13.209	서초구의 행정 구역 서초구의 행정 구역</b>은 10개의 법정동을 18개의 행정동이 관리를 하고 있다. 서초구의 면적은 47.00km2이며, 서울시의 7.8%를 차지하고 있다. 서초구의 인구는 2018년 2분기를 기준으로 443,989명, 174,268세대이다.
	10.206	로마 로마()는 이탈리아의 수도이자 라치오주의 주도로, 테베레 강 연안에 있다. 로마시의 행정구역 면적은 1,285km2로 서울시의 2배정도이고, 2014년 인구는 290여만명이다. 로마시 권역의 인구는 430여만명이다. [1] 로마 대도시현의 인구는 400만이 넘지만 밀라노나 나폴리 대도시현에 비해 면적이 3~4배 넓은 편이고 되려 로마시의 면적과 밀라노와 나폴리의 대도시현의 면적이 비슷하므로 세 도시 모두 300만 정도로 비슷한 규모의 도시라 볼 수 있다.
	6.527	율리우스 카이사르 가이우스 율리우스 카이사르(: 기원전 100년 7월 12일-기원전 44년 3월 15일)는 고대 로마의 정치가, 장군, 작가이다. 그는 로마 공화정이 제정으로 변화하는 데 중요한 역할을 하였다.

-------------------------

Top-3 Bi-Encoder Retrieval hits
	0.888	로마 로마()는 이탈리아의 수도이자 라치오주의 주도로, 테베레 강 연안에 있다. 로마시의 행정구역 면적은 1,285km2로 서울시의 2배정도이고, 2014년 인구는 290여만명이다. 로마시 권역의 인구는 430여만명이다. [1] 로마 대도시현의 인구는 400만이 넘지만 밀라노나 나폴리 대도시현에 비해 면적이 3~4배 넓은 편이고 되려 로마시의 면적과 밀라노와 나폴리의 대도시현의 면적이 비슷하므로 세 도시 모두 300만 정도로 비슷한 규모의 도시라 볼 수 있다.
	0.810	서울특별시 서울특별시(서울特別市)는 대한민국의 수도이자 최대 도시이다. 역사적으로 백제의

In [16]:
search(query = train_dataset[2]['query'])

Input question: 오대호의 크기는?
Top-3 lexical search (BM25) hits
	4.870	런던 런던 ()은 잉글랜드와 영국의 수도이자 최대 도시이다. 인구는 2014년 기준 8,538,689명으로 영국은 물론 유럽 전체 대도시권 중 가장 큰 권역이다.[주해 1] 런던은 템스 강을 기반으로 2,000년 동안 발전해 왔으며 역사는 로마인들이 론디니움이라는 요새를 지은 때부터 시작되었다.[1] 시티 오브 런던은 고대 시대부터 런던의 핵심 지역인데, 크기는 1.12-마일(2.9 km2)로 중세 시대부터 변하지 않고 있으며 2011년을 기준으로 7,375명이 거주하고 있는 잉글랜드에서 가장 작은 도시이다. 적어도 19세기부터 "런던"이라는 용어는 주변 도시를 중심으로 개발된 대도시를 뜻했다.[2] 이러한 광역 도시권의 대부분은 런던 지역[3]과 그레이터 런던으로,[4][주해 2] 런던 시장과 런던 의회에서 통치한다.[5]
	4.724	세균 세균 세포는 원형질막으로 감싸져 있다. 이 막은 세포의 기관들을 에워싸고 세포질에 있는 양분, 단백질과 다른 여러 필수적 요소들이 빠져나가지 못하게 하기 위한 하나의 벽으로써도 작용을 한다. 원핵생물이기 때문에, 세균은 세포질에 막으로 감싸진 기관들을 갖지 않으며, 크기는 크지만 적은 숫자의 세포내 구조들을 가지고 있다. 또한, 진핵 생물과 반대로 핵막과 미토콘드리아, 엽록체 같은 세포 기관도 갖지 않는다. 세균은 한 때 단순히 다량의 세포질이 뭉쳐 있는 것이라 인식되었으나, 원핵세포골격같은 구조물과 세균이 복잡한 특징을 갖게 해주고 특정 세포질 내 공간에 있는 단백질들의 위치를 확인함으로써 그렇지 않음을 알게 되었다. 이러한 세포이하수준의 조직을 세균하이퍼스트럭쳐(bacterial hyperstructure)라 일컫는다.
	4.534	혈소판 섬네일|250px|중앙 위쪽에 있는 것이 거대 혈소판이다. 좌측 귀퉁이에 보이는 조그마한 점같이 보이는 물체가 정상 혈소판이다. 혈소판(血小板, Platelet, T